In [1]:
import lightning as L
from lightning.pytorch.loggers import CSVLogger
from lightning.pytorch.callbacks import ModelCheckpoint
from torch.utils.data import DataLoader
import torch

from replay.metrics import OfflineMetrics, Recall, Precision, MAP, NDCG, HitRate, MRR
from replay.metrics.torch_metrics_builder import metrics_to_df
from replay.splitters import LastNSplitter
from replay.utils import get_spark_session
from replay.data import (
    FeatureHint,
    FeatureInfo,
    FeatureSchema,
    FeatureSource,
    FeatureType,
    Dataset,
)
from replay.models.nn.optimizer_utils import FatOptimizerFactory
from replay.models.nn.sequential.callbacks import (
    ValidationMetricsCallback,
    SparkPredictionCallback,
    PandasPredictionCallback,
    TorchPredictionCallback,
    QueryEmbeddingsPredictionCallback,
)
from replay.models.nn.sequential.postprocessors import RemoveSeenItems
from replay.data.nn import (
    SequenceTokenizer,
    SequentialDataset,
    TensorFeatureSource,
    TensorSchema,
    TensorFeatureInfo
)
from replay.models.nn.sequential import Bert4Rec
from replay.models.nn.sequential.bert4rec import (
    Bert4RecPredictionDataset,
    Bert4RecTrainingDataset,
    Bert4RecValidationDataset,
    Bert4RecPredictionBatch,
    Bert4RecModel
)

import pandas as pd

/Users/m1crozavr/Library/Caches/pypoetry/virtualenvs/movie-recommender-QIN-wZY5-py3.10/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Готовим данные

**Ноутбук выполнялся в google colab**

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
drive_path = '/content/drive/MyDrive/recsys'

In [ ]:
interactions = pd.read_csv(f'{drive_path}/data/events.csv')
item_features = pd.read_csv(f'{drive_path}/data/item_features.csv')
user_features = pd.read_csv(f'{drive_path}/data/user_features.csv')
item_features.shape, user_features.shape, interactions.shape

((3706, 19), (6040, 3), (894149, 4))

In [ ]:
# делаем чтобы не было пропусков в айтемах
# item_mapping = { item:i for i,item in enumerate(interactions['item_id'].unique())}
# item_inverse_mapping = {item:i for i,item in item_mapping.items()}
# interactions['item_id'] = interactions['item_id'].map(item_mapping)

In [ ]:
item_features = item_features.drop(columns = ['item_id']).apply(lambda row: '|'.join(item_features.columns[i+1] for i in range(len(row)) if row[i] == 1), axis=1).to_frame()
item_features['item_id'] = item_features.index
item_features.columns = ['genres', 'item_id']
item_features = item_features[['item_id', 'genres']]
item_features.head()

<ipython-input-5-46a506cb0653>:1: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  item_features = item_features.drop(columns = ['item_id']).apply(lambda row: '|'.join(item_features.columns[i+1] for i in range(len(row)) if row[i] == 1), axis=1).to_frame()


item_id                                    genres
0        0  genre_1|genre_3|genre_4|genre_8|genre_13
1        1                                   genre_7
2        2                                   genre_7
3        3                          genre_7|genre_13
4        4                                   genre_7

In [ ]:
interactions["timestamp"] = interactions["timestamp"].astype("int64")
interactions = interactions.sort_values(by="timestamp")
interactions["timestamp"] = interactions.groupby("user_id").cumcount()
interactions

user_id  item_id  rating  timestamp
831127     5596     2366       3          0
769936     5163     1160       2          0
889760     6022     1996       4          0
831058     5594     3206       3          0
259219     1747     1116       3          0
...         ...      ...     ...        ...
336760     2257     3452       3       2051
336761     2257     2749       3       2052
336762     2257     2623       3       2053
336763     2257     1175       4       2054
336764     2257     1155       2       2055

[894149 rows x 4 columns]

### Разбиение train, validation, test datasets с помощью LastNSplitter

In [ ]:
splitter = LastNSplitter(
    N=1,
    divide_column="user_id",
    query_column="user_id",
    strategy="interactions",
)

raw_test_events, raw_test_gt = splitter.split(interactions)
raw_validation_events, raw_validation_gt = splitter.split(raw_test_events)
raw_train_events = raw_validation_events

In [ ]:
# gt = ground_truth
len(raw_test_gt) + len(raw_validation_gt) + len(raw_train_events) == len(interactions)

True

In [ ]:
len(raw_train_events) + len(raw_validation_events) + len(raw_test_events), len(interactions)

(2652247, 894149)

In [ ]:
len(raw_validation_gt), len(raw_validation_events)

(6040, 882069)

### FeatureSchema

In [ ]:
def prepare_feature_schema(is_ground_truth: bool) -> FeatureSchema:
    base_features = FeatureSchema(
        [
            FeatureInfo(
                column="user_id",
                feature_hint=FeatureHint.QUERY_ID,
                feature_type=FeatureType.CATEGORICAL,
            ),
            FeatureInfo(
                column="item_id",
                feature_hint=FeatureHint.ITEM_ID,
                feature_type=FeatureType.CATEGORICAL,
            ),
        ]
    )
    if is_ground_truth:
        return base_features

    all_features = base_features + FeatureSchema(
        [
            FeatureInfo(
                column="timestamp",
                feature_type=FeatureType.NUMERICAL,
                feature_hint=FeatureHint.TIMESTAMP,
            ),
        ]
    )
    return all_features

### Dataset

In [ ]:
train_dataset = Dataset(
    feature_schema=prepare_feature_schema(is_ground_truth=False),
    interactions=raw_train_events,
    query_features=user_features,
    item_features=item_features,
    check_consistency=True,
    categorical_encoded=False,
)

### Датасеты (events and ground_truth) для валидации

In [ ]:
validation_dataset = Dataset(
    feature_schema=prepare_feature_schema(is_ground_truth=False),
    interactions=raw_validation_events,
    query_features=user_features,
    item_features=item_features,
    check_consistency=True,
    categorical_encoded=False,
)
validation_gt = Dataset(
    feature_schema=prepare_feature_schema(is_ground_truth=True),
    interactions=raw_validation_gt,
    check_consistency=True,
    categorical_encoded=False,
)

### Датасеты (events and ground_truth) для теста

In [ ]:
test_dataset = Dataset(
    feature_schema=prepare_feature_schema(is_ground_truth=False),
    interactions=raw_test_events,
    query_features=user_features,
    item_features=item_features,
    check_consistency=True,
    categorical_encoded=False,
)
test_gt = Dataset(
    feature_schema=prepare_feature_schema(is_ground_truth=True),
    interactions=raw_test_gt,
    check_consistency=True,
    categorical_encoded=False,
)

### tensor schema

In [ ]:
ITEM_FEATURE_NAME = "item_id_seq"

tensor_schema = TensorSchema(
    TensorFeatureInfo(
        name=ITEM_FEATURE_NAME,
        is_seq=True,
        feature_type=FeatureType.CATEGORICAL,
        feature_sources=[TensorFeatureSource(FeatureSource.INTERACTIONS, train_dataset.feature_schema.item_id_column)],
        feature_hint=FeatureHint.ITEM_ID,
        embedding_dim=300,
    )
)

###  SequenceTokenizer

In [ ]:
tokenizer = SequenceTokenizer(tensor_schema, allow_collect_to_master=True)
tokenizer.fit(train_dataset)

sequential_train_dataset = tokenizer.transform(train_dataset)

sequential_validation_dataset = tokenizer.transform(validation_dataset)
sequential_validation_gt = tokenizer.transform(validation_gt, [tensor_schema.item_id_feature_name])

sequential_validation_dataset, sequential_validation_gt = SequentialDataset.keep_common_query_ids(
    sequential_validation_dataset, sequential_validation_gt
)

In [ ]:
test_query_ids = test_gt.query_ids
test_query_ids_np = tokenizer.query_id_encoder.transform(test_query_ids)["user_id"].values
sequential_test_dataset = tokenizer.transform(test_dataset).filter_by_query_id(test_query_ids_np)

In [ ]:
print(tokenizer.query_id_encoder.mapping, tokenizer.query_id_encoder.inverse_mapping)
print(tokenizer.item_id_encoder.mapping, tokenizer.item_id_encoder.inverse_mapping)

{'user_id': {4855: 0, 4065: 1, 3331: 2, 5373: 3, 2032: 4, 5875: 5, 3984: 6, 4062: 7, 5117: 8, 5822: 9, 174: 10, 5188: 11, 595: 12, 2538: 13, 5031: 14, 4765: 15, 1819: 16, 3970: 17, 568: 18, 4007: 19, 2641: 20, 2646: 21, 3839: 22, 3263: 23, 281: 24, 2009: 25, 5836: 26, 1581: 27, 679: 28, 3634: 29, 2401: 30, 2184: 31, 5532: 32, 3638: 33, 4159: 34, 1770: 35, 3754: 36, 637: 37, 1452: 38, 5412: 39, 5345: 40, 3078: 41, 4772: 42, 3484: 43, 1064: 44, 2812: 45, 3120: 46, 4295: 47, 491: 48, 3283: 49, 5595: 50, 622: 51, 4428: 52, 1570: 53, 4561: 54, 3927: 55, 127: 56, 1950: 57, 1877: 58, 2285: 59, 656: 60, 462: 61, 4055: 62, 4477: 63, 2148: 64, 1582: 65, 272: 66, 3556: 67, 883: 68, 5295: 69, 3223: 70, 4070: 71, 3: 72, 5314: 73, 4225: 74, 1341: 75, 5909: 76, 1413: 77, 4463: 78, 3900: 79, 4426: 80, 811: 81, 3491: 82, 5118: 83, 2018: 84, 1308: 85, 4379: 86, 4351: 87, 2995: 88, 3680: 89, 1336: 90, 3758: 91, 1286: 92, 5003: 93, 3574: 94, 1703: 95, 1855: 96, 32: 97, 5901: 98, 5207: 99, 1516: 100, 5457:

## Train model
### обучение модели с помощью lightning

In [ ]:
MAX_SEQ_LEN = 100
BATCH_SIZE = 512
NUM_WORKERS = 4

model = Bert4Rec(
    tensor_schema,
    block_count=2,
    head_count=4,
    max_seq_len=MAX_SEQ_LEN,
    hidden_size=300,
    dropout_rate=0.5,
    optimizer_factory=FatOptimizerFactory(learning_rate=0.001),
)
checkpoint_callback = ModelCheckpoint(
    dirpath=".checkpoints",
    save_top_k=1,
    verbose=True,
    # if you use multiple dataloaders, then add the serial number of the dataloader to the suffix of the metric name.
    # For example,"recall@10/dataloader_idx_0"
    monitor="recall@10",
    mode="max",
)

validation_metrics_callback = ValidationMetricsCallback(
    metrics=["map", "ndcg", "recall"],
    ks=[1, 5, 10, 20],
    item_count=train_dataset.item_count,
    postprocessors=[RemoveSeenItems(sequential_validation_dataset)]
)

csv_logger = CSVLogger(save_dir=".logs/train", name="Bert4Rec_example")

trainer = L.Trainer(
    max_epochs=500,
    callbacks=[checkpoint_callback, validation_metrics_callback],
    logger=csv_logger,
)

train_dataloader = DataLoader(
    dataset=Bert4RecTrainingDataset(
        sequential_train_dataset,
        max_sequence_length=MAX_SEQ_LEN,
    ),
    batch_size=BATCH_SIZE,
    shuffle=True,
    num_workers=4,
    pin_memory=True,
)

validation_dataloader = DataLoader(
    dataset=Bert4RecValidationDataset(
        sequential_validation_dataset,
        sequential_validation_gt,
        sequential_train_dataset,
        max_sequence_length=MAX_SEQ_LEN,
    ),
    batch_size=BATCH_SIZE,
    num_workers=NUM_WORKERS,
    pin_memory=True,
)

trainer.fit(
    model,
    train_dataloaders=train_dataloader,
    val_dataloaders=validation_dataloader,
)

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: You are using a CUDA device ('NVIDIA A100-SXM4-40GB') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
INFO:lightning.pytorch.utilities.rank_zero:You are using a CUDA device ('NVIDIA A100-SXM4-40GB') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for p

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/lightning/pytorch/loops/fit_loop.py:298: The number of training batches (12) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

INFO: Epoch 498, global step 5988: 'recall@10' was not in top 1
INFO:lightning.pytorch.utilities.rank_zero:Epoch 498, global step 5988: 'recall@10' was not in top 1


k              1        10        20         5
map     0.040232  0.084077  0.091374  0.073245
ndcg    0.040232  0.116033  0.142778  0.089510
recall  0.040232  0.222020  0.328146  0.139404



Validation: |          | 0/? [00:00<?, ?it/s]

INFO: Epoch 499, global step 6000: 'recall@10' was not in top 1
INFO:lightning.pytorch.utilities.rank_zero:Epoch 499, global step 6000: 'recall@10' was not in top 1
INFO: `Trainer.fit` stopped: `max_epochs=500` reached.
INFO:lightning.pytorch.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=500` reached.


k              1        10        20         5
map     0.037583  0.080898  0.087838  0.069931
ndcg    0.037583  0.112627  0.137885  0.085843
recall  0.037583  0.217881  0.317715  0.134603



max на 377 эпохе

In [ ]:
best_model = Bert4Rec.load_from_checkpoint(checkpoint_callback.best_model_path)

In [ ]:
import joblib
joblib.dump(best_model, f'{drive_path}/trainedModel_long.pkl')

['/content/drive/MyDrive/recsys/trainedModel_long.pkl']

In [ ]:
import joblib
best_model = joblib.load(f'{drive_path}/trainedModel_long.pkl').to(torch.device('cpu'))

## Inference stage
### Dataloader and logger

In [ ]:
MAX_SEQ_LEN = 100
BATCH_SIZE = 512
NUM_WORKERS = 4


prediction_dataloader = DataLoader(
    dataset=Bert4RecPredictionDataset(
        sequential_test_dataset,
        max_sequence_length=MAX_SEQ_LEN,
    ),
    batch_size=BATCH_SIZE,
    num_workers=NUM_WORKERS,
    pin_memory=True,
)

csv_logger = CSVLogger(save_dir=".logs/test", name="Bert4Rec_example")

### Run inference
результат в 3 форматах: PySpark DataFrame, Pandas DataFrame, PyTorch tensors. Each of the types corresponds a callback
Добавляем RemoveSeenItems, чтобы отфильтровать что уже было в датасете

In [ ]:
TOPK = [1, 10, 20, 100]

# postprocessors = [RemoveSeenItems(sequential_test_dataset)]

pandas_prediction_callback = PandasPredictionCallback(
    top_k=max(TOPK),
    query_column="user_id",
    item_column="item_id",
    rating_column="score",
    # postprocessors=postprocessors,
)


query_embeddings_callback = QueryEmbeddingsPredictionCallback()

trainer = L.Trainer(
    callbacks=[
        pandas_prediction_callback,
        query_embeddings_callback
    ],
    logger=csv_logger,
    inference_mode=True
)
trainer.predict(best_model, dataloaders=prediction_dataloader, return_predictions=False)

pandas_res = pandas_prediction_callback.get_result()
user_embeddings = query_embeddings_callback.get_result()

INFO: GPU available: True (cuda), used: True
INFO:lightning.pytorch.utilities.rank_zero:GPU available: True (cuda), used: True
INFO: TPU available: False, using: 0 TPU cores
INFO:lightning.pytorch.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO: HPU available: False, using: 0 HPUs
INFO:lightning.pytorch.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO: LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:lightning.pytorch.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |          | 0/? [00:00<?, ?it/s]

In [ ]:
pandas_res.head()

user_id item_id     score
0      790    1422  8.709385
0      790    2003  7.775912
0      790    2543  7.253259
0      790    1014  7.075572
0      790    1259  6.737379

In [ ]:
recommendations = tokenizer.query_and_item_id_encoder.inverse_transform(pandas_res)

In [ ]:
recommendations.head()

user_id  item_id     score
0        0     1422  8.709385
0        0     2003  7.775912
0        0     2543  7.253259
0        0     1014  7.075572
0        0     1259  6.737379

In [ ]:
merged_df = recommendations.merge(interactions[['user_id', 'item_id']], on = ['user_id', 'item_id'], how = 'left', indicator = True)
result = merged_df[merged_df['_merge'] == 'left_only'].drop(columns = ['_merge'])

In [ ]:
(result.groupby('user_id')['score'].count() < 10).sum()

0

In [ ]:
result_filtered_df = result.sort_values('score', ascending=False).groupby('user_id')['item_id'].apply(
    lambda item_ids: ' '.join(map(str, item_ids.tolist()[:10]))
)
result_filtered_df

user_id
0       1422 2003 2543 1014 1259 1101 1052 2551 3421 1287
1         232 1246 2476 1686 350 3101 1813 2730 1459 1822
2           2774 1781 234 382 1560 2424 2311 221 2428 887
3           1560 1893 989 467 2564 487 1501 304 1100 1052
4            983 755 672 394 1160 2237 3530 1044 2338 304
                              ...                        
6035    1011 3668 2800 2256 3059 1403 3382 2502 2366 1102
6036      3692 3142 1859 2528 3105 2470 2054 2732 922 494
6037      2664 1375 1747 133 2256 3656 611 1593 1102 3059
6038           3605 797 316 3222 450 3055 84 2608 49 1893
6039          870 3551 3364 1098 215 654 936 1593 383 190
Name: item_id, Length: 6040, dtype: object

In [ ]:
result_filtered_df.reset_index().to_csv(f'{drive_path}/submit_brt_no_postproc.csv', header=True, index=False)